## Multi-tree objects
Toytree also supports the use of `multitree` objects to store lists of linked trees, such as bootstrap replicates or trees sampled from a posterior distribution. `multitree` objects can be generated by parsing a file or string of newick trees separated by newlines. 

In [55]:
import toytree
import toyplot
import numpy as np

An example multi-tree newick file represented as a string:

In [30]:
string = """\
(((a:1,b:1):1,(d:1.5,e:1.5):0.5):1,c:3);
(((a:1,d:1):1,(b:1,e:1):1):1,c:3);
(((a:1.5,b:1.5):0.5,(d:1,e:1):1):1,c:3);
(((a:1.25,b:1.25):0.75,(d:1,e:1):1):1,c:3);
(((a:1,b:1):1,(d:1.5,e:1.5):0.5):1,c:3);
(((a:1,b:1):1,(d:1.5,e:1.5):0.5):1,c:3);
(((a:1.5,b:1.5):0.5,(d:1,e:1):1):1,c:3);
(((b:1.5,d:1.5):0.5,(a:1,e:1):1):1,c:3);
"""

Parse the multi-tree newick string as a `multitree` object:

In [31]:
trees = toytree.multitree(string)

You can access each individual tree from the `multitree` object's `treelist` attribute. Unlike regular Toytree objects these trees will have *their tip order fixed* so that discordance between trees is apparent. This is important for creating cloudtrees, further below. 

In [34]:
for tre in trees.treelist:
    tre.draw(tree_style='c', use_edge_lengths=True)

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

d e a b c 
 
 
 Save as .csv

### Consensus tree

A `multitree` object can return an unrooted consensus tree as a `toytree` object. 


In [35]:
## returns the majority 50% tree 
constree = trees.get_consensus_tree(cutoff=0.50)

## returns the extended majority-rule consensus tree
constree = trees.get_consensus_tree()

In [38]:
## it is unrooted so I shift the node labels to the edges
constree.draw(
    width=200, 
    node_labels=constree.get_node_values("support"), 
    node_size=0,
    node_labels_style={
        'font-size': '12px',
        '-toyplot-anchor-shift': '-20px',
        'baseline-shift': '10px'
        }
    );

c d e a b 100 75 75 
 
 
 Save as .csv

### Draw a cloud-tree
Cloud trees are useful for representing discordance or variation among a set of trees. You can draw a cloudtree from a multitree object using the `draw_cloudtree()` function, which has similar arguments as the standard `draw()` function. 

In [41]:
trees.draw_cloudtree(
    width=200,
    orient='right',
    use_edge_lengths=True,
    edge_style={"opacity": 0.3}
    );

d e a b c 
 
 
 Save as .csv

### Empirical example

In this example we'll load an mcmc file from a species tree analysis in the program BPP which includes a sample of species trees sampled from a posterior distribution. 

In [113]:
## btw, your input newick files can be a weblink
mcmcfile = "https://dl.dropboxusercontent.com/u/2538935/full-r0.mcmc.txt"
trees = toytree.multitree(mcmcfile)
print "{} trees".format(len(trees))

2001 trees


First you can examine a consensus tree. 

In [114]:
## get consens tree
ctre = trees.get_consensus_tree()

## draw with supports
ctre.draw(node_labels=ctre.get_node_values("support"));

prz cys cya sup cup tha rck lip rex 100 100 100 100 98 60 56 
 
 
 Save as .csv

Again we'll load the data from the mcmc file from a species tree analysis in the program BPP. For plotting cloud-trees often such a file will contain too many trees to display clearly, and so we can use the `treeslice` argument to subsample them. In the example below we sample every 10th tree between 10-4000. 

In [115]:
mcmcfile = "https://dl.dropboxusercontent.com/u/2538935/full-r0.mcmc.txt"
trees = toytree.multitree(mcmcfile, treeslice=(10, 4000, 10))
print "{} trees".format(len(trees))

200 trees


With default options the cloud tree doesn't look too bad. 

In [116]:
trees.draw_cloudtree(
    width=300,
    orient='right',
    use_edge_lengths=True,
    );

<g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opac

And of course you can dress it up a bit nicer with better tip labels, and by adjusting the opacity of edges on the tree. 

In [117]:
tips = [
    "<em>P. przewalskii</em>",
    "<em>P. cyathophylloides</em>",
    "<em>P. cyathophylla</em>",
    "<em>P. superba</em>",
    "<em>P. thamnophila cup.</em>",
    "<em>P. thamnophila tham.</em>",
    "<em>P. rex rockii</em>",
    "<em>P. rex rex</em>",
    "<em>P. rex lipskyana</em>",
]

In [118]:
## plot the tree
trees.draw_cloudtree(
    width=400, 
    height=350,
    orient='right',
    edge_style={"opacity": 0.05},
    use_edge_lengths=True,
    tip_labels=tips[::-1],
    );

<g cl

Finally, you can plot the tree onto a set of Toyplot axes for finer control and the ability to add things like axis labels. 

In [119]:
## set up axes
canvas = toyplot.Canvas(width=500, height=350)
axes1 = canvas.cartesian(bounds=(50, 300, 50, 300))
axes2 = canvas.cartesian(bounds=(300, 500, 50, 300))

## add tree
trees.draw_cloudtree(
    axes=axes1,
    orient='right',
    use_edge_lengths=True,
    tip_labels=False,
    edge_style={
        'opacity': 0.025, 
        'stroke': '#262626'},
    );

## add tip labels
tre = trees.treelist[0]
axes2.text(
    np.zeros(len(tre)), 
    tre.verts[-1*len(tre):, 1],
    tips[::-1],
    style={
        'text-anchor': 'start',
        '-toyplot-anchor-shift': '-25px',
        'fill': '#262626',
        },
    );

## axis styling
axes1.y.show = False
axes1.x.ticks.show = True
axes1.x.ticks.locator = toyplot.locator.Explicit(
    locations=np.linspace(0, -15, 5) / 1000.,
    labels=np.linspace(0, 15, 5),
    )
axes1.x.label.text = axes.x.label.text = "Divergence time (substitutions/site x 10<sup>-3</sup>)"
axes2.show = False

<g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opaci

#### Save the plots


In [107]:
toyplot.html.render(canvas, "cloud-test.html")
import toyplot.svg
toyplot.svg.render(canvas, "cloud-test.svg")

### Attributes of the Multitree object
Below I list all of the attributes of a multitree object. In a notebook you can use tab-completion to see of all of these. 

In [ ]:
## draws a cloudtree (returns (canvas, axes))
## with options similar to draw()
trees.draw_cloudtree()

In [ ]:
## returns a consensus tree
trees.get_consensus_tree()

In [121]:
## returns the newick string, file, or url
trees.newick

'https://dl.dropboxusercontent.com/u/2538935/full-r0.mcmc.txt'

In [127]:
## a list of Toytree objects in this multitree object
## I show just the first 10 here.
trees.treelist[:10]

In [120]:
## a conveniently accessible list of pretty colors
trees.colors

['rgba(40.0%,76.1%,64.7%,1.000)',
 'rgba(98.8%,55.3%,38.4%,1.000)',
 'rgba(55.3%,62.7%,79.6%,1.000)',
 'rgba(90.6%,54.1%,76.5%,1.000)',
 'rgba(65.1%,84.7%,32.9%,1.000)',
 'rgba(100.0%,85.1%,18.4%,1.000)',
 'rgba(89.8%,76.9%,58.0%,1.000)',
 'rgba(70.2%,70.2%,70.2%,1.000)']